<a href="https://colab.research.google.com/github/bvsdinda/TPE-LSTM/blob/main/Hyperparameter_tuning_best.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import statsmodels.api as smi
from sklearn import preprocessing
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
from statistics import mean
import tensorflow as tf
from tensorflow.keras.models import load_model
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, SimpleRNN, GRU, Dropout, Conv1D, MaxPooling1D, Flatten, RepeatVector
from sklearn.metrics import mean_squared_error, r2_score, mean_absolute_percentage_error, mean_absolute_error
from tensorflow.keras.optimizers import Adam, Nadam, RMSprop
from statsmodels.tsa.seasonal import seasonal_decompose
from keras.callbacks import EarlyStopping
from keras.callbacks import ModelCheckpoint
from hyperopt import hp, Trials, fmin, tpe
import joblib
import warnings
warnings.simplefilter('ignore')

In [ ]:
df=pd.read_csv('Bank.csv')
df.head(5)

Date    AXISBANK   AXISVOL  BAJAJFIN  BAJAJFINVOL        BOB  \
0  02-01-2009  108.379997  14261265  6.310420       141738  57.340000   
1  05-01-2009  112.019997   9165605  6.504736      1120575  58.860001   
2  06-01-2009  113.949997  12893855  6.660189       312830  57.750000   
3  07-01-2009  104.419998  10571555  6.150109       166223  54.939999   
4  09-01-2009   97.320000  25173105  6.048093        95905  54.689999   

    BOBVOL    FEDBANK   FEDVOL        HDFC  ...      KOTAK  KOTAKVOL  \
0  1700495  16.889999  1359910  101.565002  ...  97.900002   6258884   
1  2687100  17.129999  4379460  104.410004  ...  99.637497   5956956   
2  3162520  16.760000  1930260  110.040001  ...  96.712502   9015300   
3  5602350  16.459999  2251090  100.925003  ...  90.762497   6482408   
4  1806325  16.004999  4046570  101.750000  ...  86.125000   5076276   

          PNB   PNBVOL         SBI    SBIVOL        REC   RECVOL     PIRAMAL  \
0  106.430000  2973855  133.184998  24161650  29.587500  9574565  134.700485   
1  107.160004  3037185  136.080002  26931910  30.562500  8844514  136.025497   
2  106.089996  4110100  132.285004  35970960  29.831249  1078005  133.516418   
3   97.660004  6538860  124.004997  37268580  28.424999  5624090  131.853104   
4   97.129997  3834090  122.110001  24996510  28.818750  6157634  129.654144   

   PIRAMALVOL  
0      222908  
1       14449  
2      102783  
3       24863  
4      301873  

[5 rows x 25 columns]

In [ ]:
feature_columns = ['SBI', 'SBIVOL']
target_column = ['SBI']
features = df[feature_columns]
target = df[target_column].shift(-1)
new_data1 = 758.30
target.iloc[-1, 0] = new_data1
target.tail(5)

SBI
3748  746.700012
3749  740.049988
3750  733.299988
3751  752.349976
3752  758.300000

In [ ]:
scaler = MinMaxScaler(feature_range=(0, 1))
scaled_features = scaler.fit_transform(features)
scaled_target = scaler.fit_transform(target.values.reshape(-1, 1))

n_steps = 5  # Number of timesteps to look back
X, y = [], []

for i in range(n_steps, len(scaled_features)):
    X.append(scaled_features[i-n_steps:i])
    y.append(scaled_target[i])

X = np.array(X)
y = np.array(y)

split=int(0.8*len(X))
X_train, y_train= X[:split], y[:split]
X_test, y_test= X[split:], y[split:]

In [ ]:
def create_model_lstm(params):
  model_lstm = tf.keras.Sequential()
  model_lstm.add(tf.keras.layers.LSTM(units=int(params['units']), activation='relu', input_shape=(X_train.shape[1], X_train.shape[2]), return_sequences=params['return_sequences']))
  if params['return_sequences'] == 'False':
    params['n_layers'] = 1
    model_lstm.add(tf.keras.layers.LSTM(units=int(params['units']), activation='relu', input_shape=(X_train.shape[1], X_train.shape[2]), return_sequences=False))
  elif params['return_sequences'] == 'True':
    params['n_layers'] = 2
    model_lstm.add(tf.keras.layers.LSTM(units=int(params['units']), activation='relu', input_shape=(X_train.shape[1], X_train.shape[2]), return_sequences=True))
    model_lstm.add(tf.keras.layers.LSTM(units=int(params["units1"]), activation='relu', return_sequences=params['return_sequences1']))
    if params['return_sequences1'] == 'False':
      params['n_layers'] = 2
      model_lstm.add(tf.keras.layers.LSTM(units=int(params['units']), activation='relu', input_shape=(X_train.shape[1], X_train.shape[2]), return_sequences=True))
      model_lstm.add(tf.keras.layers.LSTM(units=int(params["units1"]), activation='relu', return_sequences=False))
    elif params['return_sequences1'] == 'True':
      params['n_layers'] = 3
      model_lstm.add(tf.keras.layers.LSTM(units=int(params['units']), activation='relu', input_shape=(X_train.shape[1], X_train.shape[2]), return_sequences=True))
      model_lstm.add(tf.keras.layers.LSTM(units=int(params['units1']), activation='relu', return_sequences=True))
      model_lstm.add(tf.keras.layers.LSTM(units=int(params['units2']), activation='relu', return_sequences=False))
  model_lstm.add(tf.keras.layers.Dense(units=1))
  model_lstm.compile(loss='mse', optimizer=Nadam(learning_rate=params['learning_rate']))
  return model_lstm

In [ ]:
# Define objective function
def objective_function(params):
  model = create_model_lstm(params)
  model.fit(X_train, y_train, epochs=params['epochs'], batch_size=int(params['batch_size']), callbacks=[EarlyStopping(monitor='loss', patience=3)])
  loss = model.evaluate(X_test, y_test)
  return loss

# Define search space
search_space = {
  'units': hp.quniform('units', 32, 512, 1 ),
  'units1': hp.quniform('units1', 32, 512, 1 ),
  'units2': hp.quniform('units2', 32, 512, 1 ),
  #'units3': hp.quniform('units3', 32, 512, 1 ),
  #'units4': hp.quniform('units4', 32, 512, 1),
  #'units5': hp.quniform('units5', 32, 512, 1 ),
  'n_layers': hp.choice('n_layers', [1, 2, 3]),
  'return_sequences': hp.choice('return_sequences', [True, False]),
  'return_sequences1': hp.choice('return_sequences1', [True, False]),
  'learning_rate': hp.loguniform('learning_rate', np.log(0.0001), np.log(0.01)),
  'epochs': hp.choice('epochs', [200]),
  'batch_size': hp.quniform('batch_size', 16, 128, 1),
}

# Initialize trials and optimizer
trials = Trials()
best_params = fmin(fn=objective_function, space=search_space, algo=tpe.suggest, max_evals=60, trials=trials)
# Print best parameters
print(f"Best parameters: {best_params}")

  0%|          | 0/60 [00:00<?, ?trial/s, best loss=?]

Epoch 1/200

49/49 [==============================] - 4s 12ms/step - loss: 0.0028

Epoch 2/200

49/49 [==============================] - 1s 18ms/step - loss: 2.4877e-04

Epoch 3/200

49/49 [==============================] - 1s 18ms/step - loss: 2.5365e-04

Epoch 4/200

49/49 [==============================] - 1s 16ms/step - loss: 2.4569e-04

Epoch 5/200

49/49 [==============================] - 1s 15ms/step - loss: 2.9891e-04

Epoch 6/200

49/49 [==============================] - 1s 15ms/step - loss: 2.4113e-04

Epoch 7/200

49/49 [==============================] - 1s 14ms/step - loss: 2.6797e-04

Epoch 8/200

49/49 [==============================] - 1s 11ms/step - loss: 2.4483e-04

Epoch 9/200

49/49 [==============================] - 1s 12ms/step - loss: 2.3466e-04

Epoch 10/200

49/49 [==============================] - 1s 11ms/step - loss: 2.1557e-04

Epoch 11/200

49/49 [==============================] - 1s 11ms/step - loss: 2.0980e-04

Epoch 12/200

49/49 [========================

Epoch 1/200

30/30 [==============================] - 2s 12ms/step - loss: 0.0094

Epoch 2/200

30/30 [==============================] - 0s 11ms/step - loss: 0.0012

Epoch 3/200

30/30 [==============================] - 0s 11ms/step - loss: 7.1443e-04

Epoch 4/200

30/30 [==============================] - 0s 11ms/step - loss: 5.2217e-04

Epoch 5/200

30/30 [==============================] - 0s 11ms/step - loss: 4.1941e-04

Epoch 6/200

30/30 [==============================] - 0s 13ms/step - loss: 3.5217e-04

Epoch 7/200

30/30 [==============================] - 0s 12ms/step - loss: 3.0688e-04

Epoch 8/200

30/30 [==============================] - 0s 12ms/step - loss: 2.9546e-04

Epoch 9/200

30/30 [==============================] - 0s 12ms/step - loss: 2.8366e-04

Epoch 10/200

30/30 [==============================] - 0s 12ms/step - loss: 2.8471e-04

Epoch 11/200

30/30 [==============================] - 0s 11ms/step - loss: 2.7885e-04

Epoch 12/200

30/30 [============================

Epoch 1/200

26/26 [==============================] - 2s 10ms/step - loss: 0.0359

Epoch 2/200

26/26 [==============================] - 0s 11ms/step - loss: 0.0062

Epoch 3/200

26/26 [==============================] - 0s 10ms/step - loss: 0.0022

Epoch 4/200

26/26 [==============================] - 0s 10ms/step - loss: 9.7813e-04

Epoch 5/200

26/26 [==============================] - 0s 11ms/step - loss: 2.9752e-04

Epoch 6/200

26/26 [==============================] - 0s 10ms/step - loss: 2.4272e-04

Epoch 7/200

26/26 [==============================] - 0s 11ms/step - loss: 2.3759e-04

Epoch 8/200

26/26 [==============================] - 0s 10ms/step - loss: 2.3607e-04

Epoch 9/200

26/26 [==============================] - 0s 10ms/step - loss: 2.3408e-04

Epoch 10/200

26/26 [==============================] - 0s 11ms/step - loss: 2.3243e-04

Epoch 11/200

26/26 [==============================] - 0s 11ms/step - loss: 2.3287e-04

Epoch 12/200

26/26 [==============================] 

Epoch 1/200

28/28 [==============================] - 2s 11ms/step - loss: 0.0418

Epoch 2/200

28/28 [==============================] - 0s 10ms/step - loss: 0.0257

Epoch 3/200

28/28 [==============================] - 0s 10ms/step - loss: 0.0115

Epoch 4/200

28/28 [==============================] - 0s 11ms/step - loss: 0.0046

Epoch 5/200

28/28 [==============================] - 0s 11ms/step - loss: 0.0030

Epoch 6/200

28/28 [==============================] - 0s 11ms/step - loss: 0.0022

Epoch 7/200

28/28 [==============================] - 0s 10ms/step - loss: 0.0015

Epoch 8/200

28/28 [==============================] - 0s 12ms/step - loss: 9.3130e-04

Epoch 9/200

28/28 [==============================] - 0s 11ms/step - loss: 5.5795e-04

Epoch 10/200

28/28 [==============================] - 0s 11ms/step - loss: 3.7970e-04

Epoch 11/200

28/28 [==============================] - 0s 11ms/step - loss: 3.0769e-04

Epoch 12/200

28/28 [==============================] - 0s 11ms/step -

...

Epoch 1/200

28/28 [==============================] - 4s 23ms/step - loss: 0.0278

Epoch 2/200

28/28 [==============================] - 1s 21ms/step - loss: 0.0026

Epoch 3/200

28/28 [==============================] - 1s 22ms/step - loss: 8.5130e-04

Epoch 4/200

28/28 [==============================] - 1s 21ms/step - loss: 2.7134e-04

Epoch 5/200

28/28 [==============================] - 1s 21ms/step - loss: 2.5046e-04

Epoch 6/200

28/28 [==============================] - 0s 16ms/step - loss: 2.4693e-04

Epoch 7/200

28/28 [==============================] - 1s 20ms/step - loss: 2.4737e-04

Epoch 8/200

28/28 [==============================] - 1s 18ms/step - loss: 2.4507e-04

Epoch 9/200

28/28 [==============================] - 1s 19ms/step - loss: 2.4341e-04

Epoch 10/200

28/28 [==============================] - 1s 18ms/step - loss: 2.4203e-04

Epoch 11/200

28/28 [==============================] - 0s 17ms/step - loss: 2.4264e-04

Epoch 12/200

28/28 [============================

Epoch 1/200

70/70 [==============================] - 4s 20ms/step - loss: 0.0105

Epoch 2/200

70/70 [==============================] - 1s 20ms/step - loss: 0.0012

Epoch 3/200

70/70 [==============================] - 1s 19ms/step - loss: 6.6083e-04

Epoch 4/200

70/70 [==============================] - 1s 20ms/step - loss: 4.8110e-04

Epoch 5/200

70/70 [==============================] - 2s 23ms/step - loss: 3.7135e-04

Epoch 6/200

70/70 [==============================] - 2s 24ms/step - loss: 3.1133e-04

Epoch 7/200

70/70 [==============================] - 2s 26ms/step - loss: 2.9028e-04

Epoch 8/200

70/70 [==============================] - 2s 23ms/step - loss: 2.9181e-04

Epoch 9/200

70/70 [==============================] - 1s 20ms/step - loss: 2.8431e-04

Epoch 10/200

70/70 [==============================] - 1s 21ms/step - loss: 2.9023e-04

Epoch 11/200

70/70 [==============================] - 2s 21ms/step - loss: 2.9078e-04

Epoch 12/200

70/70 [============================

Epoch 1/200

63/63 [==============================] - 4s 17ms/step - loss: 0.0072

Epoch 2/200

63/63 [==============================] - 1s 18ms/step - loss: 5.8812e-04

Epoch 3/200

63/63 [==============================] - 1s 20ms/step - loss: 2.7712e-04

Epoch 4/200

63/63 [==============================] - 1s 19ms/step - loss: 2.5819e-04

Epoch 5/200

63/63 [==============================] - 1s 20ms/step - loss: 2.5045e-04

Epoch 6/200

63/63 [==============================] - 1s 20ms/step - loss: 2.3858e-04

Epoch 7/200

63/63 [==============================] - 1s 18ms/step - loss: 2.3144e-04

Epoch 8/200

63/63 [==============================] - 1s 18ms/step - loss: 2.2528e-04

Epoch 9/200

63/63 [==============================] - 1s 19ms/step - loss: 2.1987e-04

Epoch 10/200

63/63 [==============================] - 1s 18ms/step - loss: 2.1611e-04

Epoch 11/200

63/63 [==============================] - 1s 17ms/step - loss: 2.1038e-04

Epoch 12/200

63/63 [========================

Epoch 1/200

150/150 [==============================] - 6s 17ms/step - loss: 0.0016

Epoch 2/200

150/150 [==============================] - 3s 17ms/step - loss: 2.7047e-04

Epoch 3/200

150/150 [==============================] - 3s 18ms/step - loss: 2.5745e-04

Epoch 4/200

150/150 [==============================] - 3s 20ms/step - loss: 2.4495e-04

Epoch 5/200

150/150 [==============================] - 3s 17ms/step - loss: 2.3364e-04

Epoch 6/200

150/150 [==============================] - 3s 17ms/step - loss: 2.2288e-04

Epoch 7/200

150/150 [==============================] - 3s 17ms/step - loss: 1.9945e-04

Epoch 8/200

150/150 [==============================] - 2s 16ms/step - loss: 1.9103e-04

Epoch 9/200

150/150 [==============================] - 2s 16ms/step - loss: 1.8116e-04

Epoch 10/200

150/150 [==============================] - 2s 17ms/step - loss: 1.8786e-04

Epoch 11/200

150/150 [==============================] - 3s 18ms/step - loss: 1.7179e-04

Epoch 12/200

150/150 [

Epoch 1/200

112/112 [==============================] - 5s 16ms/step - loss: 0.0022

Epoch 2/200

112/112 [==============================] - 2s 16ms/step - loss: 2.5064e-04

Epoch 3/200

112/112 [==============================] - 2s 15ms/step - loss: 2.5593e-04

Epoch 4/200

112/112 [==============================] - 2s 16ms/step - loss: 2.7220e-04

Epoch 5/200

112/112 [==============================] - 2s 16ms/step - loss: 2.2241e-04

Epoch 6/200

112/112 [==============================] - 2s 17ms/step - loss: 2.2151e-04

Epoch 7/200

112/112 [==============================] - 2s 17ms/step - loss: 2.1625e-04

Epoch 8/200

112/112 [==============================] - 2s 18ms/step - loss: 2.0505e-04

Epoch 9/200

112/112 [==============================] - 2s 16ms/step - loss: 1.9996e-04

Epoch 10/200

112/112 [==============================] - 2s 16ms/step - loss: 1.8426e-04

Epoch 11/200

112/112 [==============================] - 2s 16ms/step - loss: 1.8591e-04

Epoch 12/200

112/112 [